# Comparaison linéaire entre zeop et ban

In [4]:
import numpy as np
import pandas as pd
import openpyxl

In [5]:
Ban_Adress = pd.read_excel("./Adresses BAN Les 3 Bassins.xlsx")
Zeop_Adress = pd.read_excel("./Adresses ZEOP Les 3 Bassins.xlsx")

In [6]:
# Import necessary packages
import folium
from folium import plugins


In [50]:
map = folium.Map(location=(Zeop_Adress['y'].mean(), Zeop_Adress['x'].mean()), zoom_start=14, tiles='https://server.arcgisonline.com/ArcGIS/rest/services/World_Imagery/MapServer/tile/{z}/{y}/{x}', attr='Esri')

test_zeop = Zeop_Adress[['y', 'x', 'num_voie', 'type_voie', 'nom_voie']].to_numpy()
for lat, lon, num_voie, type_voie, nom_voie in test_zeop:
    folium.Circle(
        location=[lat,lon],
        radius=3,  # Taille du point
        color='red',  # Couleur de la bordure
        weight=2,  # Épaisseur de la bordure (toujours en mètres pour `folium.Circle`)
        fill=True,  # Remplissage du point
        fill_color='red',  # Couleur de remplissage
        fill_opacity=0.3,  # Opacité
        popup = f"{num_voie} {type_voie} {nom_voie}"
    ).add_to(map)

Cert_Ban_Adress = Ban_Adress[Ban_Adress['certification_commune'] == 1]
test_ban = Cert_Ban_Adress[['lat', 'lon', 'numero', 'nom_voie']].to_numpy()
for lat, lon, num, nom_voie in test_ban:
    folium.Circle(
        location=[lat,lon],
        radius=3,  # Taille du point
        color='green',  # Couleur de la bordure
        weight=2,  # Épaisseur de la bordure (toujours en mètres pour `folium.Circle`)
        fill=True,  # Remplissage du point
        fill_color='green',  # Couleur de remplissage
        fill_opacity=0.3,  # Opacité
        popup = f"{num} {nom_voie}"
    ).add_to(map)
map

In [ ]:
from scipy.spatial import cKDTree
# Extraction des coordonnées géographiques
erreur_zeop = Zeop_Adress[Zeop_Adress['nom_voie'] == 'DES JASMINS'].copy()
zeop_coords = erreur_zeop[['y', 'x']].to_numpy()  # y = latitude, x = longitude
ban_coords = Ban_Adress[['lat', 'lon']].to_numpy()  # lat = latitude, lon = longitude

# Construction d'un arbre KD à partir des coordonnées BAN
tree = cKDTree(ban_coords)

# Recherche du point le plus proche pour chaque point ZEOP
distances, indices = tree.query(zeop_coords)

# Ajout des résultats au DataFrame ZEOP
erreur_zeop['nearest_lat'] = ban_coords[indices][:, 0]  # Latitude du point le plus proche
erreur_zeop['nearest_lon'] = ban_coords[indices][:, 1]  # Longitude du point le plus proche
erreur_zeop['distance'] = distances  # Distance au point le plus proche

map2 = folium.Map(location=(erreur_zeop['y'].mean(), erreur_zeop['x'].mean()), zoom_start=20)

test_zeop = erreur_zeop[['y', 'x', 'num_voie', 'type_voie', 'nom_voie']].to_numpy()
for lat, lon, num_voie, type_voie, nom_voie in test_zeop:
    folium.Circle(
        location=[lat,lon],
        radius=3,  # Taille du point
        color='red',  # Couleur de la bordure
        weight=2,  # Épaisseur de la bordure (toujours en mètres pour `folium.Circle`)
        fill=True,  # Remplissage du point
        fill_color='red',  # Couleur de remplissage
        fill_opacity=0.3,  # Opacité
        popup = f"{num_voie} {type_voie} {nom_voie}"
    ).add_to(map2)
erreur_ban = Ban_Adress[(Ban_Adress['lat'].isin(erreur_zeop['nearest_lat'])) & (Ban_Adress['lon'].isin(erreur_zeop['nearest_lon']))].copy()
test_ban = erreur_ban[['lat', 'lon', 'numero', 'nom_voie']].to_numpy()
for lat, lon, numero, nom_voie in test_ban:
    folium.Circle(
        location=[lat,lon],
        radius=3,  # Taille du point
        color='green',  # Couleur de la bordure
        weight=2,  # Épaisseur de la bordure (toujours en mètres pour `folium.Circle`)
        fill=True,  # Remplissage du point
        fill_color='green',  # Couleur de remplissage
        fill_opacity=0.3,  # Opacité
        popup = f"{numero} {nom_voie}"
    ).add_to(map2)
map2